In [1]:
import pandas as pd
from pathlib import Path
from ydata_profiling import ProfileReport
from scripts.data.data_acquisition import DataAcquisition

In [2]:
PATH_DATA = Path("data")
compiled_data = DataAcquisition.compile_data(PATH_DATA)
compiled_data.head()

id                                              title condition  \
0  MCO1324022622          Pila Recargables Aa X2 Energizer 2000 Mah       new   
1  MCO1271613775       Pila Energizer Recharge Universal Aaa X 4und       new   
2  MCO1037658202  Audífonos In-ear Inalámbricos Bluetooth F9-5 N...       new   
3  MCO1343307899    Televisor 43 Pulgadas Smart Android Ref. 43lo69       new   
4  MCO1318891937  Parlante Jbl Flip 6 Portátil Con Bluetooth Wat...       new   

  catalog_product_id listing_type_id  \
0        MCO21850181    gold_special   
1        MCO22015422    gold_special   
2        MCO16224063    gold_special   
3        MCO26796977        gold_pro   
4        MCO18930465    gold_special   

                                           permalink buying_mode site_id  \
0  https://www.mercadolibre.com.co/pila-recargabl...  buy_it_now     MCO   
1  https://www.mercadolibre.com.co/pila-energizer...  buy_it_now     MCO   
2  https://www.mercadolibre.com.co/audifonos-in-e...  buy_it_now     MCO   
3  https://www.mercadolibre.com.co/televisor-43-p...  buy_it_now     MCO   
4  https://www.mercadolibre.com.co/parlante-jbl-f...  buy_it_now     MCO   

  category_id           domain_id  ...  shipping_promise   seller_id  \
0     MCO7279  MCO-CELL_BATTERIES  ...               NaN   199769978   
1     MCO7279  MCO-CELL_BATTERIES  ...               NaN   199769978   
2     MCO3697      MCO-HEADPHONES  ...               NaN  1066063779   
3    MCO14903     MCO-TELEVISIONS  ...               NaN   388583366   
4     MCO3691        MCO-SPEAKERS  ...               NaN   478332182   

       seller_nickname  installments_quantity installments_amount  \
0          OPERADOR TO                   36.0              647.47   
1          OPERADOR TO                   36.0             1039.64   
2   JUAN20220131132107                    NaN                 NaN   
3    CHALLENGER S.A.S.                   12.0            81658.33   
4  IXCOMERCIO COLOMBIA                   36.0            11525.00   

   installments_rate installments_currency_id    brand_value_name location  \
0                0.0                      COP           Energizer      NaN   
1                0.0                      COP           Energizer      NaN   
2                NaN                      NaN  Shenzhen Yihaotong      NaN   
3                0.0                      COP          Challenger      NaN   
4                0.0                      COP                 JBL      NaN   

  seller_contact  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  

[5 rows x 36 columns]

In [4]:
ProfileReport(compiled_data, minimal=True)#.to_file("data_report.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

* id : Sin necesidad de cambios
* title : Sin necesidad de cambios (Podría hacerse después algo con NLP para utilizar los títulos como input para el descuento)
* condition : Hay múltiples articulos con el condition en null (lo cual es diferente a que no esté especificado, ya que, esto tiene su propia categoría de not_specified). REVISAR POR QUÉ RAZÓN LLEGARON NULOS
* catalog_product_id : El poseer un valor, quiere decir que el producto está incluido en algún catalogo. Podría convertirse en una variable binaria que me permita saber si un artículo se encuentra en algún catalogo o no https://developers.mercadolibre.com.ar/es_ar/que-es-catalogo
* listing_type_id : Sin necesidad de cambios (O bueno, podría revisarse si transformar esta variable considerando la ordinalidad de los datos) https://api.mercadolibre.com/sites/MCO/listing_types#options - https://www.mercadolibre.com.co/ayuda/Obten_r-mas-visitas_680 - https://www.mercadolibre.com.co/ayuda/Costos-de-vender-productos_870
* permalink: se elimina antes del análisis
* buying_mode: sin cambios. Es importante tener en cuenta que aquí puede existir para otros países la categoría de auction, solo que en Colombia actualmente no existe
* site_id: Para esta iteración se puede eliminar, ya que todos son de Colombia
* category_id: Se elimina, contiene un desglose más alto de las cateogrías del producto. Es mejor conservar unicamente la categoría de la variable category que es con la que se fueron filtrando y extrayendo los productos
* domain_id: También se elimina, es un nivel de detalle demasiado alto para buscar predecirlo con este tipo de nivel (Tal vez se podría considerar para otra iteración, ya que dentro de una categoría están los domain)
* price y original_price: En caso de que no hayan datos en price, quiere decir que es una publicación (seguramente de un servicio) donde el precio es a convenir (EJ: https://servicio.mercadolibre.com.co/MCO-1339589647-multiservicios-cb-especialistas-en-inyeccion-y-electronica-m-_JM). Adicionalmente, para los casos donde original_price no tiene valor pero si tiene valor la columna de price, quiere decir que el artículo no tiene descuento. Hay que revisar manualmente los valores más bajos ya que pueden generar bastante ruido (o no), hay publicaciones extrañas, como por ejemplo, un supermercado en venta por 1400 pesos https://inmueble.mercadolibre.com.co/MCO-2214055384-supermercado-en-venta-negocio-en-venta-_JM o también casas super grandes por 9999999999 https://casa.mercadolibre.com.co/MCO-2047055060-casa-en-venta-medellin-sector-poblado-_JM
* available quantity: Sin cambios (Evaluar el tema de outliers porque pueden haber productos con demasiado stock)
* official_store_id: SIn cambios pero se puede remover, no sirve como feature, pero revisar si puede cruzarse con algunas información de store que sea relevante. Revisar si el hecho de no tener algún id de tienda oficinal, quiere decir que es un vendedor como persona jurídica con su tiendita y no una tienda oficial vendiendo a través de mercadolibre
* accepts_mercadopago: Sin cambios, revisar porque esta variable está ultra desbalanceada (Rta: Esto se debe a que los productos que no aceptan mercadopago son aquellos que tienen que ver con contactar el vendedor, por ejemplo, productos de las categorías de 'MCO1459', 'MCO1540', 'MCO1743', que corresponden a inmuebles, servicios y carros, motos y otros)) Gráfico de acepta mercadopago o no de acuerdo a cada una de las categorías de producto. También si proporción de si tiene o no descuento
* stop_time: Extraer de aquí la cantidad de días hasta el vencimiento de la publicación para ver si se puede utilizar este número para generar categorías (Ej: publicaciones que se terminan en 30 días contra publicaciones que se terminan en 3 años) o incluso para colocar un techo a los días máximos de una publicación
* catalog_listing: Sin cambios. Representa si un artículo dado se encuentra incluido en un catalogo o no
* promotions: La variable no tiene nada importante. Eliminar
* category: Se queda, tal vez se debería de cambiar con algún encoding y cambiar los códigos de categorías por los nombres de categorías
* shipping_store_pick_up: Se elimina, no hay ningún articulo que deje recoger en tienda en Colombia
* shipping_free_shipping: Sin cambios
* shipping_logistic_type: Revisar que significa cada una de las categorías, pero se puede quedar https://developers.mercadolibre.com.co/es_ar/mercadoenvios-modo-2 https://developers.mercadolibre.com.co/es_ar/envio-personalizado
* shipping_mode: Es una versión más resumida de shipping_logistic_type ya que trata solo sobre mercado envios 1, mercado envios 2 y custom (envios personalizados por el cliente). Considerar usar esta en lugar de shipping_logistic_type en caso de que no sea tan buena
* shipping_tags: Eliminar porque ya es demasiado detalle acerca de los envíos de ML
* shipping_benefits: Eliminar, todos son nulos
* shipping_promise: Eliminar, todos son nulos
* seller_id: Conservar para buscarlos nuevamente con la API y obtener características del vendedor como por ejemplo su reputación y utilizarlo como input para modelar
* seller_nickname: Podría eliminarse
* installments_quantity: Conservar. Puede ser llenar los nulos con cero ya que esto quiere decir que no es posible tener compra a cuotas en el producto
* installments_amount: Podría eliminarse porque está asociada también con el numero de cuotas de un producto y con el precio que este tiene
* installments_rate: Eliminar para el caso de Colombia, porque parece que la tasa es de cero para todoss ya que esto no lo define directamente mercadolibre sino el banco emisor de la TC con la que se busque comprar un artículo
* installments_currency_id: Eliminar. Irrelevante porque para todo Colombia va a ser COP
* brand_value_name: Revisar si conservar o no, hay muchísimos nombres de marca e incluso hay varios que están mal escritos
* location: Eliminar. Muchos nulos
* seller_contact: Eliminar. Muchos nulos y parece irrelevante

In [11]:
compiled_data[compiled_data.accepts_mercadopago == False]["category"].unique()#.iloc[2000]

array(['MCO1459', 'MCO1540', 'MCO1743'], dtype=object)

In [38]:
compiled_data[compiled_data.catalog_listing == True]["price"].iloc[5]

999900.0

In [ ]:
compiled_data[compiled_data.catalog_listing == True]["price"].iloc[5]

In [ ]:
from scripts.data.api_access import call_access_token, refresh_access_token
from scripts.data.secrets.api_access_data import client_secret, app_id, refresh_token
response = refresh_access_token(client_secret, app_id, refresh_token)
call_access_token()
#https://api.mercadolibre.com/items/MCO1271613775/health

In [6]:
from requests import request

In [9]:
item_id = "MCO1271613775"
url = f"https://api.mercadolibre.com/reviews/item/{item_id}"

access_token = call_access_token()
payload = {}
headers = {'Authorization': f'Bearer {access_token}'}

response = request("GET", url, headers=headers, data=payload)

print(response.text)


{"paging":{"total":50,"limit":5,"offset":0,"kvs_total":50},"reviews":[{"id":1018375137,"reviewable_object":{"id":"MCO1271613775","type":"product"},"date_created":"2024-02-22T21:57:06Z","status":"published","title":"Excelente","content":"Muy practicas y duran bastante.","rate":5,"valorization":0,"likes":0,"dislikes":0,"reviewer_id":0,"buying_date":"2023-12-08T20:04:25Z","relevance":5,"forbidden_words":0,"attributes":null,"media":[],"reactions":null,"attributes_variation":null},{"id":835447118,"reviewable_object":{"id":"MCO1271613775","type":"product"},"date_created":"2023-12-04T12:02:52Z","status":"published","title":"Muy malo","content":"La peor compra!!, a los 2 meses ya no duran mas de 3 minutos, no pierdan su plata 🤢🤮🤮🤮.","rate":1,"valorization":1,"likes":1,"dislikes":0,"reviewer_id":0,"buying_date":"2023-05-10T22:24:33Z","relevance":18,"forbidden_words":20,"attributes":null,"media":[],"reactions":null,"attributes_variation":null},{"id":973907797,"reviewable_object":{"id":"MCO127161